# 生物情報の解析 2

In [ ]:
# GoogleドライブにあるファイルをColabで読み書きできるようにする
# google.colab: Google Colabのためのライブラリ
# drive: Googleドライブに接続するためのモジュール
# '/content/drive': Google ドライブを接続（マウント）したときに使われる仮想的なフォルダ
# drive.mountでは、'/content/drive'以外のフォルダを指定することは推奨されていない
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
# os: OS（オペレーティングシステム）に関する操作を行うためのモジュール
# os.name（OSの種類を示す変数） を入力すると、Google Colabの場合、'posix'が表示される
# chdir: 作業ディレクトリの変更（設定）
import os
os.chdir('/content/drive/MyDrive/bio/')

In [ ]:
# matplotlib: データの可視化をインタラクティブに行うライブラリ
# pyplot: グラフ描画を行うモジュール
# matplotlibライブラリのpyplotモジュールをpltという名前で取り込む
import matplotlib.pyplot as plt
# japanize-matplotlib: 日本語の文字表示に対応したライブラリ（matplotlibは日本語の文字表示に対応していないためインストールが必要）
!pip install japanize-matplotlib
# japanize-matplotlibライブラリのjapanize_matplotlibモジュールを取り込む
# これにより、matplotlibのフォント設定が自動的に変更され、日本語が表示できるようになる
import japanize_matplotlib
# 上記でうまくいかない場合は、以下の関数を実行する
# japanize_matplotlib.japanize()

**BioPythonのインストール**

In [ ]:
!pip install --upgrade biopython

## モチーフ

In [ ]:
from Bio import motifs    # 配列のモチーフを扱う専門ライブラリ
from Bio.Seq import Seq
import numpy as np
name = "tata.txt"
f = open(name, 'r')
ali=[]
i = 0
for line in f.readlines():
  line = line.replace("\n", "")     # 改行文字が入っていると、配列オブジェクトの生成がうまくいかない
  ali.append(Seq(line))
  print(line)
m = motifs.create(ali)      # リストからモチーフの生成

In [ ]:
m.counts      # 各カラムの塩基の出現カウント、各列は配列位置

In [ ]:
# コンセンサス配列
m.consensus

In [ ]:
m.weblogo(
    "tata.png",
    format="png_print",
#    resolution=600,
    errorbars=False,
    show_errorbars=False,
    barbits=False,
    annotate=" ",
    fineprint=" "
)     # 指定したファイルに画像を出力

In [ ]:
from IPython.display import Image

Image("tata.png")

In [ ]:
# position weight matrix （実は頻度行列？、m.countsを全配列数で割ったもの）
m.pwm

In [ ]:
m.background

In [ ]:
pwm = m.counts.normalize(pseudocounts={'A': 0.25, 'C': 0.25, 'G': 0.25, 'T': 0.25})
# (f(i,j)+0.25)/(10+1) ←修正-- f(i,j)/10

In [ ]:
# m.pssm でも同じ結果
pwm

In [ ]:
pssm = pwm.log_odds()
pssm

In [ ]:
# print("%4.2f" % pssm.max)
# print("%4.2f" % pssm.min)

In [ ]:
test_seq=Seq("TACACGTCATTACTGTACCTATGTTACGTATTA",m.alphabet)    # 配列オブジェクト, m.alphabet = 'ACGT'
test_seq

In [ ]:
# PWMを用いてスコアリングと検索
for pos in range(len(test_seq) - len(m) + 1):  # シーケンスをスライド
    subseq = test_seq[pos:pos + len(m)]
    score = pwm.log_odds(m.background).calculate(subseq)  # PWMスコアを計算
    print(f"位置: {pos}, 部分配列: {subseq}, スコア: {score}")

In [ ]:
score = pssm.calculate(test_seq)      # 各配列位置の一致スコアを並べたもの
score

In [ ]:
len(score), len(test_seq)

In [ ]:
# モチーフ検索を実装
threshold = 0.0  # 必要に応じて閾値を設定
for pos in range(len(test_seq) - len(m) + 1):  # シーケンスをスライド
    subseq = test_seq[pos:pos + len(m)]
    score = pwm.log_odds(m.background).calculate(subseq)  # PWMスコアを計算
    if score > threshold:  # 閾値を超えた場合、モチーフと一致した部分の候補
        print(f"位置: {pos}, 部分配列: {subseq}, スコア: {score}")

# 平均情報量（情報エントロピー）

In [ ]:
# モチーフの機能も使えるようだが、Colabで使えるバージョンには制限があったため、計算式通りに計算

import numpy as np

# file_path = "rox1p.txt"
# file_path = "pribnow.txt"
file_path = "ecoli-codon.txt"
# file_path = "ecoli-upstream.txt"
# file_path = "ecoli-promoter.txt"

def read_dna_sequences(file_path):
    sequences = []
    with open(file_path, 'r') as file:
        for line in file:
            # Assume each line in the file is a DNA sequence.
            # Strip any whitespace or newline characters.
            sequence = line.strip().upper()
            # Validate the sequence and add it to the list
            if all(nucleotide in 'ACGT' for nucleotide in sequence):
                sequences.append(sequence)
            else:
                print(f"Invalid sequence found: {sequence}")
    return sequences

def calculate_entropy(sequences):
    # Initialize a list to hold the entropy of each position
    entropy_list = []

    # Transpose the list of sequences to get a list of all characters at each position
    transposed = np.array([list(seq) for seq in sequences]).T

    # Calculate the entropy for each position
    for position in transposed:
        # Count the frequency of each nucleotide in the current position
        counts = np.array([np.count_nonzero(position == nucleotide) for nucleotide in 'ACGT'])
        # Calculate the probabilities
        probabilities = counts / len(sequences)
        # Ensure that we don't include zero probabilities in the entropy calculation
        probabilities = probabilities[probabilities > 0]
        # Calculate the entropy for the current position
        entropy = -np.sum(probabilities * np.log2(probabilities))
        # Append the entropy to the list
        entropy_list.append(entropy)

    return entropy_list

sequences = read_dna_sequences(file_path)
# Calculate entropy for each position
entropies = calculate_entropy(sequences)
entropies


In [ ]:
import matplotlib.pyplot as plt
n = len(entropies)
plt.figure(figsize=(10, 5))  # Set the figure size
plt.plot(entropies, marker='o')  # Plot the values with circle markers
# plt.xticks(range(0, n, int(n/10)))
plt.yticks(np.arange(0,2.1,0.5))
plt.title('Entropy of each position')  # Title of the graph
plt.xlabel('Position')  # X-axis label
plt.ylabel('Entropy')  # Y-axis label
plt.grid(True)  # Show grid
plt.show()  # Display the plot



BioPythonの機能を使う

In [ ]:
from Bio import motifs
from Bio.Seq import Seq

instances = [Seq(s) for s in sequences]
m = motifs.create(instances)

m.weblogo(
    "logo.png",
    format="png_print",
    resolution=600,
    errorbars=False,
    show_errorbars=False,
    barbits=False,
    annotate=" ",
    fineprint=" "
)


In [ ]:
from IPython.display import Image

Image("logo.png")

# 分子系統樹の作成

In [ ]:
!apt-get update
!apt-get install -y clustalo
!clustalo -i seqs.fasta -o aligned.fasta --force

In [ ]:
!clustalo -i cytoC.fasta -o cytoC_aligned.fasta --force

In [ ]:
from Bio import AlignIO, Phylo
from Bio.Phylo.TreeConstruction import DistanceCalculator, DistanceTreeConstructor
import matplotlib.pyplot as plt

# アラインメント読み込み
alignment = AlignIO.read("cytoC_aligned.fasta", "fasta")

# 距離行列の作成
calculator = DistanceCalculator("identity")
dm = calculator.get_distance(alignment)

# UPGMAE法と NJ 法 の両方を試してみよう
constructor = DistanceTreeConstructor()
# tree = constructor.nj(dm)
tree = constructor.upgma(dm)

# 系統樹描画
plt.figure(figsize=(10, 8))
Phylo.draw(tree)


# シグナルペプチド予測

In [ ]:
import pandas as pd
import numpy as np
from array import array
from collections import Counter
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import ExtraTreesClassifier
from sklearn.metrics import accuracy_score, roc_auc_score

# PROTEIN_ALPHABET = "ACDEFGHIKLMNPQRSTVWY"
# PROTEIN_ORD_TABLE = ord_table(PROTEIN_ALPHABET)

# 学習用（訓練用）
pos_filename = "signal-positive.txt"
neg_filename = "signal-negative.txt"
# Read positives
pos_label = 1
neg_label = 0

# アミノ酸のアルファベット
PROTEIN_ALPHABET = "ACDEFGHIKLMNPQRSTVWY"

def make_freq_table(filename, label):
# 各文字列に対して文字の出現頻度を計算し、結果をリストに保存
    freq_list = []
    with open(filename, "r") as file:
        for line in file:
            # 改行を除去し、文字列を取得
            seq = line.strip()
            l = len(seq)
            freq = [seq.count(letter) / l for letter in PROTEIN_ALPHABET]
            freq = freq + [label]
            freq_list.append(freq)
    return freq_list


# def feature_importance(X, y):
#     clf_ = ExtraTreesClassifier(n_estimators=50)
#     clf_ = clf_.fit(X, y)
#     return clf_.feature_importances_

pos_freq = make_freq_table(pos_filename, pos_label)
neg_freq = make_freq_table(neg_filename, neg_label)
freq_data = pos_freq + neg_freq
freq_data = np.asarray(freq_data)
# print(freq_data)
# Save data to csv
df_data = pd.DataFrame(freq_data, columns=list(PROTEIN_ALPHABET)+['label'])
# df_data = pd.DataFrame(freq_data)
df_data.to_csv("data.csv", index=False)

# Split dataset
state = 42
t_size = 0.3
X, y = freq_data[:, :-1], freq_data[:, -1]
# X = df_data.drop('label', axis=1)
# y = df_data['label']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=t_size, random_state=state)

# print(X)
# print(X_test)
# print(y_test)
# モデルの準備
model = DecisionTreeClassifier(max_depth=5)
# model = ExtraTreesClassifier(n_estimators=50)

# 学習データセットでの学習の実行
model.fit(X_train, y_train)
# 学習データセットでの予測の実行
model.predict(X_train)
print('正解率(train):{:.3f}'.format(model.score(X_train, y_train)))
# テストデータセットでの予測の実行
y_pred = model.predict(X_test)
print('正解率(test):{:.3f}'.format(model.score(X_test, y_test)))

acc_value = accuracy_score(y_test, y_pred)
auc_value = roc_auc_score(y_test, y_pred)
print(f"ACC: {acc_value:.3f} AUC: {auc_value:.3f}")



In [ ]:

import matplotlib.pyplot as plt
import graphviz
from sklearn import tree
# from sklearn.tree import plot_tree
# plot_tree(model, feature_names=X_train.columns, class_names=True, filled=True)
graph = graphviz.Source(tree.export_graphviz(model, feature_names=df_data.drop(['label'],axis=1).columns, filled=True))
graph

In [ ]:
features = pd.DataFrame(model.feature_importances_, index=df_data.drop(['label'],axis=1).columns)
features.sort_values(0,ascending=False)

**シグナルペプチド予測（ExtraTreeを利用）**

In [ ]:
import pandas as pd
import numpy as np
from array import array
from collections import Counter
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import ExtraTreesClassifier
from sklearn.metrics import accuracy_score, roc_auc_score

# PROTEIN_ALPHABET = "ACDEFGHIKLMNPQRSTVWY"
# PROTEIN_ORD_TABLE = ord_table(PROTEIN_ALPHABET)

# 学習用（訓練用）
pos_filename = "signal-positive.txt"
neg_filename = "signal-negative.txt"
# Read positives
pos_label = 1
neg_label = 0

# アミノ酸のアルファベット
PROTEIN_ALPHABET = "ACDEFGHIKLMNPQRSTVWY"

def make_freq_table(filename, label):
# 各文字列に対して文字の出現頻度を計算し、結果をリストに保存
    freq_list = []
    with open(filename, "r") as file:
        for line in file:
            # 改行を除去し、文字列を取得
            seq = line.strip()
            l = len(seq)
            freq = [seq.count(letter) / l for letter in PROTEIN_ALPHABET]
            freq = freq + [label]
            freq_list.append(freq)
    return freq_list


def feature_importance(X, y):
    clf_ = ExtraTreesClassifier(n_estimators=50)
    clf_ = clf_.fit(X, y)
    return clf_.feature_importances_

pos_freq = make_freq_table(pos_filename, pos_label)
neg_freq = make_freq_table(neg_filename, neg_label)
freq_data = pos_freq + neg_freq
freq_data = np.asarray(freq_data)
# print(freq_data)
# Save data to csv
df_data = pd.DataFrame(freq_data, columns=list(PROTEIN_ALPHABET)+['label'])
# df_data = pd.DataFrame(freq_data)
df_data.to_csv("data.csv", index=False)

# Split dataset
state = 42
t_size = 0.3
X, y = freq_data[:, :-1], freq_data[:, -1]
# X = df_data.drop('label', axis=1)
# y = df_data['label']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=t_size, random_state=state)

# print(X)
# print(X_test)
# print(y_test)
# モデルの準備
# model = DecisionTreeClassifier()
model = ExtraTreesClassifier(n_estimators=50)

# 学習データセットでの学習の実行
model.fit(X_train, y_train)
# 学習データセットでの予測の実行
model.predict(X_train)
print('正解率(train):{:.3f}'.format(model.score(X_train, y_train)))
# テストデータセットでの予測の実行
y_pred = model.predict(X_test)
print('正解率(test):{:.3f}'.format(model.score(X_test, y_test)))

acc_value = accuracy_score(y_test, y_pred)
auc_value = roc_auc_score(y_test, y_pred)
print(f"ACC: {acc_value:.3f} AUC: {auc_value:.3f}")

# For training data, compute tree-based feature importance
fi = feature_importance(X_train, y_train)
dict_fi = {}
for aa, f in zip(PROTEIN_ALPHABET, fi):
    dict_fi[aa] = f
# sort the dict of feature importance
print("Feature importance of 20 amino acids")
for k, v in sorted(dict_fi.items(), key=lambda item: item[1], reverse=True):
    print(f"{k} - {v:.3f}")